In [23]:
! pip install replicate requests aiohttp python-dotenv Pillow pyfs

^C


In [ ]:
import asyncio
from collections import defaultdict
import json
import aiohttp
import requests
import os
from dotenv import load_dotenv

load_dotenv()

last_fm_api_base_url = "http://ws.audioscrobbler.com/2.0/"


def get_top_200_last_fm_artists():
    top_200_last_fm_artists = []
    for page_number in range(1, 5):
        fifty_top_artists = requests.get(last_fm_api_base_url + "?method=chart.gettopartists&api_key=" + os.environ["LAST_FM_API_KEY"] + "&format=json&page=" + str(page_number)).json()
        for artist in fifty_top_artists["artists"]["artist"]:
            top_200_last_fm_artists.append(artist["name"])
    return top_200_last_fm_artists



def get_top_three_albums_for_all_artists(artists):
    top_three_albums = defaultdict(list)
    for artist in artists:
        top_three_albums[artist] = [album["name"] for album in requests.get(last_fm_api_base_url + "?method=artist.gettopalbums&artist=" + artist + "&api_key=" + os.environ["LAST_FM_API_KEY"] + "&format=json&limit=3").json()["topalbums"]["album"]]
    return top_three_albums


def generate_urls_to_get_top_three_albums(top_three_albums_for_artists):
    urls = []
    for artist, albums in top_three_albums_for_artists.items():
        for album in albums:
            urls.append(last_fm_api_base_url + "?method=album.getinfo&api_key=" + os.environ["LAST_FM_API_KEY"] + "&artist=" + artist + "&album=" + album + "&format=json")
    return urls


urls = generate_urls_to_get_top_three_albums(get_top_three_albums_for_all_artists(get_top_200_last_fm_artists()))

json.dump(urls, open("urls.json", "w+"), indent = 4, ensure_ascii=False)

KeyboardInterrupt: 

In [6]:
async def get_album_with_info(session, url):
    async with session.get(url) as response:
        return await response.json()


async def get_albums_with_info(urls):
    async with aiohttp.ClientSession() as session:
        albums_with_info = [get_album_with_info(session, url) for url in urls]
        return await asyncio.gather(*albums_with_info)


urls = json.load(open("urls.json"))
albums_with_info = await get_albums_with_info(urls)
json.dump(albums_with_info, open("albums_with_info.json", "w+"), indent = 4, ensure_ascii=False)

_GatheringFuture exception was never retrieved
future: <_GatheringFuture finished exception=RuntimeError('Session is closed')>
Traceback (most recent call last):
  File "/var/folders/sm/t27sm5ds1wd7mk1xbywlh7xw0000gn/T/ipykernel_1446/3283206036.py", line 2, in get_album_with_info
    async with session.get(url) as response:
  File "/Users/christopher/Documents/PycharmProjects/collage-album-cover-generator/.venv/lib/python3.12/site-packages/aiohttp/client.py", line 1344, in __aenter__
    self._resp = await self._coro
                 ^^^^^^^^^^^^^^^^
  File "/Users/christopher/Documents/PycharmProjects/collage-album-cover-generator/.venv/lib/python3.12/site-packages/aiohttp/client.py", line 481, in _request
    raise RuntimeError("Session is closed")
RuntimeError: Session is closed


[{'album': {'artist': 'Billie Eilish', 'mbid': '033ddd2b-d499-426e-872a-697a1b5ca0c2', 'tags': {'tag': [{'url': 'https://www.last.fm/tag/electropop', 'name': 'electropop'}, {'url': 'https://www.last.fm/tag/pop', 'name': 'pop'}, {'url': 'https://www.last.fm/tag/ambient+pop', 'name': 'ambient pop'}, {'url': 'https://www.last.fm/tag/indie+pop', 'name': 'indie pop'}, {'url': 'https://www.last.fm/tag/2010s', 'name': '2010s'}]}, 'playcount': '102861590', 'image': [{'size': 'small', '#text': 'https://lastfm.freetls.fastly.net/i/u/34s/c2652de4809e5b4349565518b34b85ca.jpg'}, {'size': 'medium', '#text': 'https://lastfm.freetls.fastly.net/i/u/64s/c2652de4809e5b4349565518b34b85ca.jpg'}, {'size': 'large', '#text': 'https://lastfm.freetls.fastly.net/i/u/174s/c2652de4809e5b4349565518b34b85ca.jpg'}, {'size': 'extralarge', '#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/c2652de4809e5b4349565518b34b85ca.jpg'}, {'size': 'mega', '#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/c2652de4809e5

In [17]:
import random

albums_with_info = json.load(open("albums_with_info.json"))

def get_ten_albums_with_info_by_genre(genre):
    albums_with_info_by_genre = []
    while len(albums_with_info_by_genre) < 10:
        try:
            random_album = albums_with_info[random.randint(0, albums_with_info.__len__() - 1)]
            tags = []
            for tag in random_album["album"]["tags"]["tag"]:
                tags.append(tag["name"])
            if genre in tags:
                albums_with_info_by_genre.append({ "name": random_album["album"]["name"], "artist": random_album["album"]["artist"], "image_url": random_album["album"]["image"][4]["#text"]})
        except (KeyError, TypeError):
            pass
    return albums_with_info_by_genre


ten_albums_with_info_by_genre = get_ten_albums_with_info_by_genre(input("Enter a genre:"))

In [40]:
import json
import replicate
from PIL import Image, ImageChops
import fs
from io import BytesIO
import os
import requests
import random

os.environ["REPLICATE_API_TOKEN"]

def getRandomSegment(url):

    input = {
        "image": url,
        "mask_limit": 5,
        "mask_2_mask": False, 
        "crop_n_layers": 0,
        "points_per_side": 64,
        "stability_score_thresh": 0.5,
    }

    output = replicate.run(
        "lucataco/segment-anything-2:be7cbde9fdf0eecdc8b20ffec9dd0d1cfeace0832d4d0b58a071d993182e1be0",
        input=input
    )

    input_response = requests.get(input.get("image"))
    input_image = Image.open(BytesIO(input_response.content)).convert("RGBA")

    for i, mask_url in enumerate(output):
        output_response = requests.get(mask_url)
        mask = Image.open(BytesIO(output_response.content)).convert("L")  # Convert to grayscale

        bbox = mask.getbbox()
        if bbox:
            non_transparent_area = mask.crop(bbox)
            print(f"Mask {i} non-transparent area dimensions: {non_transparent_area.size}")
        else:
            print(f"Mask {i} is fully transparent")

    # Create a binary mask
        binary_mask = mask.point(lambda p: p > 128 and 255)
        
    # Composite the images using the binary mask
        composite_image = Image.composite(input_image, Image.new("RGBA", input_image.size), binary_mask)
        compatible_masks = []
    # Save or show the composite image
        mask_area = composite_image.crop(mask.getbbox()).height * composite_image.crop(mask.getbbox()).width
        composite_image.save(f"composite_image_{i}.png")
        if mask_area > 100:
            compatible_masks.append(composite_image)
    random_number = random.randint(0, len(compatible_masks) - 1)

    print('hi', input.get("image"))
    print(json.dumps(output))
    return compatible_masks[random_number]

getRandomSegment('https://th.bing.com/th/id/OIP.QT_ze_xwLmxbepdySxndMQHaHa?rs=1&pid=ImgDetMain').show()

Mask 0 non-transparent area dimensions: (474, 474)
Mask 1 non-transparent area dimensions: (102, 67)
Mask 2 non-transparent area dimensions: (390, 373)
Mask 3 non-transparent area dimensions: (45, 46)
Mask 4 non-transparent area dimensions: (15, 18)


NameError: name 'random' is not defined